In [1]:
using FileIO;
using LibSndFile;
using Plots;
using DSP;
using SampledSignals;
using FixedPointNumbers;
using CUDA

In [2]:
tetris = load("tetris_piano_mono.wav");
fs = round(Int,tetris.samplerate);
tetris.data = tetris.data[1:(10*fs),:];
original = Float32.(tetris.data[:,1] .+ tetris.data[:,2]);
tetris

441000-frame, 2-channel SampleBuf{Q0f15, 2}
10.0s sampled at 44100.0Hz
▁▁▅▅▄▄▃▆▅▆▆▆▆▅▆▆▆▆▆▆▅▆▆▅▅▅▆▆▆▆▅▆▅▄▃▆▆▅▆▆▆▆▅▅▅▅▄▆▆▅▆▅▅▅▅▆▅▄▃▆▆▅▅▅▆▆▅▅▅▆▆▅▅▅▅▄▄▃▃▂
▁▁▆▆▅▄▄▆▅▆▅▆▅▅▆▆▆▅▅▅▅▆▅▅▄▄▆▅▆▅▅▆▅▅▄▆▅▅▆▅▅▅▅▄▄▄▄▅▅▅▆▅▅▄▆▆▅▅▄▆▅▅▅▄▆▅▅▅▄▆▅▅▄▄▄▄▄▃▃▃

Analysis Filter Bank

In [27]:
LA = FIRFilter([0,0.25,0.5,0.25,0],1//2);
HA = FIRFilter([-0.125,-0.25,0.75,-0.25,-0.125],1//2);
LS = FIRFilter([-0.25,0.5,1.5,0.5,-0.25],2//1);
HS = FIRFilter([0,-0.5,1,-0.5,0],2//1);

In [31]:
x = [original];
for octave ∈ 1:3
    y = copy(x);
    append!(y,[[]]);
    y[end-1] = filt(HA, x[end]);
    y[end] = filt(LA, x[end]);
    x = y;
end

In [32]:
size.(x)

4-element Vector{Tuple{Int64}}:
 (220500,)
 (110250,)
 (55125,)
 (55125,)

Synthesis Filter Bank

In [33]:
for octave ∈ 1:3
    y = copy(x[1:end-1]);
    y[end] = filt(LS, x[end]) .+ filt(HS, x[end-1]);
    x = y
end

In [34]:
R = Q0f15.(x[1]);

In [35]:
recovered = copy(tetris);
recovered.data = hcat(R,R);
recovered

441000-frame, 2-channel SampleBuf{Q0f15, 2}
10.0s sampled at 44100.0Hz
▂▁▇▇▆▅▄▇▆▇▇▇▇▆▇▇▇▇▆▇▆▇▇▆▆▆▇▆▇▇▆▇▆▆▅▇▇▆▇▆▇▇▆▆▆▅▅▇▇▆▇▆▆▆▆▇▆▆▅▇▇▆▆▆▇▆▆▆▆▆▆▆▆▆▅▅▅▄▄▄
▂▁▇▇▆▅▄▇▆▇▇▇▇▆▇▇▇▇▆▇▆▇▇▆▆▆▇▆▇▇▆▇▆▆▅▇▇▆▇▆▇▇▆▆▆▅▅▇▇▆▇▆▆▆▆▇▆▆▅▇▇▆▆▆▇▆▆▆▆▆▆▆▆▆▅▅▅▄▄▄

In [38]:
test = Float32.(collect(1:16))

16-element Vector{Float32}:
  1.0
  2.0
  3.0
  4.0
  5.0
  6.0
  7.0
  8.0
  9.0
 10.0
 11.0
 12.0
 13.0
 14.0
 15.0
 16.0

In [39]:
filt(LS,test)

32-element Vector{Float64}:
 -0.250786155462265
  0.4996885061264038
  1.000155746936798
  1.5
  2.0
  2.5
  3.0
  3.5
  4.0
  4.5
  5.0
  5.5
  6.0
  ⋮
 10.0
 10.5
 11.0
 11.5
 12.0
 12.5
 13.0
 13.5
 14.0
 14.5
 15.0
 15.5